In [8]:
import pandas as pd
metadata = pd.read_csv('sample-metadata.tsv', sep='\t')
#display(metadata)
with open('category.txt', 'r') as f:
    category = f.readline().rstrip()
display(metadata[category])

0      before
1      before
2      before
3      before
4      before
        ...  
408     after
409     after
410     after
411     after
412    before
Name: group, Length: 413, dtype: object

In [9]:
import pandas as pd
import glob, os
from pathlib import Path

### Celda que combina todos los archivos de alfa diversidad en una unica tabla de formato wide-mixed
### Tambien combina con metadata y exporta a alpha-out-proyecto.tsv

### busco nombre de proyecto
dataset = Path(os.getcwd()).stem

### Leo metadata, nombre de primer columna para copiar sample-id
metadata = pd.read_csv('sample-metadata.tsv', sep='\t')
tag = metadata.columns[0]

### leo tsv en carpeta, guardo en arreglo, renombro
alphas = []
for file in glob.glob("./qiime/alphas/*.tsv"):
    tmp = pd.read_csv(file, sep='\t')
    tmp.rename( columns={'Unnamed: 0':tag}, inplace=True ) 
    alphas.append(tmp)

### combino columnas de archivos individuales, genero unica tabla
diversities = alphas[0]
for dataframe in alphas[1:]:
    diversities = pd.merge(diversities, dataframe)
diversities.drop('osd', axis=1, inplace=True, errors='ignore')
metrics = list(diversities.columns[1:])
#print(metrics)

### Leo sample frenquency y combino
sample_freq = pd.read_csv('qiime/sample-frequency-detail.csv', names= [tag, 'sample-frequency'])
diversities = pd.merge(diversities, sample_freq)

### combino con metadata
metadata.drop_duplicates(subset=tag, keep='first', inplace = True)
complete = diversities.merge(metadata, on=tag, how='inner')
complete.insert(0,'folder', dataset)

## Agrego columna con grupos
complete.insert(1,'dataset', dataset + "_" + complete[category])

### exporto a archivo
filename = "alpha-out." + dataset + ".tsv"
complete.to_csv(filename, sep='\t', index=False)
#print(complete.columns)
display(complete)

folder             dataset   sample-id         ace  berger_parker_d  \
0    248_citizen  248_citizen_before  sample-129   88.549766         0.271275   
1    248_citizen   248_citizen_after  sample-287   88.000000         0.269825   
2    248_citizen  248_citizen_before  sample-197  218.569297         0.319665   
3    248_citizen   248_citizen_after  sample-489   63.000000         0.305966   
4    248_citizen  248_citizen_before    sample-1  102.967524         0.157426   
..           ...                 ...         ...         ...              ...   
408  248_citizen   248_citizen_after  sample-272   80.093405         0.202097   
409  248_citizen  248_citizen_before  sample-180   69.687801         0.404839   
410  248_citizen   248_citizen_after  sample-337  114.038117         0.097931   
411  248_citizen  248_citizen_before   sample-82  125.967508         0.360709   
412  248_citizen  248_citizen_before  sample-148  127.681337         0.236174   

     brillouin_d       chao1  dominance  doubles     enspie  ...  sample_name  \
0       3.106930   88.333333   0.101662        2   9.836561  ...   ERS1418043   
1       3.038018   88.000000   0.100976        6   9.903308  ...   ERS1418204   
2       3.242708  215.444444   0.119166       26   8.391657  ...   ERS1418111   
3       2.585680   63.000000   0.130351       11   7.671615  ...   ERS1418406   
4       3.103065  102.000000   0.079538        9  12.572642  ...   ERS1417911   
..           ...         ...        ...      ...        ...  ...          ...   
408     2.898990   78.833333   0.091664       11  10.909407  ...   ERS1418188   
409     2.393982   69.333333   0.193366        2   5.171543  ...   ERS1418094   
410     3.637120  112.333333   0.040169       11  24.894563  ...   ERS1418254   
411     2.629755  123.647059   0.167911       16   5.955538  ...   ERS1417995   
412     3.388120  126.600000   0.079921        9  12.512294  ...   ERS1418062   

     Sequencing_method  SRA_accession  SRA Study  \
0       16S sequencing     ERS1418043  ERP018192   
1       16S sequencing     ERS1418204  ERP018192   
2       16S sequencing     ERS1418111  ERP018192   
3       16S sequencing     ERS1418406  ERP018192   
4       16S sequencing     ERS1417911  ERP018192   
..                 ...            ...        ...   
408     16S sequencing     ERS1418188  ERP018192   
409     16S sequencing     ERS1418094  ERP018192   
410     16S sequencing     ERS1418254  ERP018192   
411     16S sequencing     ERS1417995  ERP018192   
412     16S sequencing     ERS1418062  ERP018192   

                                title  host_subject_id  INSDC_center_alias  \
0    Healthy human gut 16S metagenome      subject3353                 NaN   
1    Healthy human gut 16S metagenome      subject1765                 NaN   
2    Healthy human gut 16S metagenome      subject3443                 NaN   
3    Healthy human gut 16S metagenome      subject3493                 NaN   
4    Healthy human gut 16S metagenome       subject168                 NaN   
..                                ...              ...                 ...   
408  Healthy human gut 16S metagenome       subject439                 NaN   
409  Healthy human gut 16S metagenome      subject3424                 NaN   
410  Healthy human gut 16S metagenome      subject3279                 NaN   
411  Healthy human gut 16S metagenome      subject3282                 NaN   
412  Healthy human gut 16S metagenome      subject3376                 NaN   

     run_accession      numID   group  
0       ERR1700291  6967.5176  before  
1       ERR1700449  2203.8952   after  
2       ERR1700359  6250.6991  before  
3       ERR1700651  7034.1173   after  
4       ERR1699775  2281.4816  before  
..             ...        ...     ...  
408     ERR1700434  3342.0816   after  
409     ERR1700342  3679.3767  before  
410     ERR1700499  6189.1553   after  
411     ERR1700244  4433.1757  before  
412     ERR1700310  3142.0442  before  

[413 rows x 79 column

In [10]:
import plotly.express as px

figbox = px.box(complete, x=category, y=metrics,
             facet_col ="variable", color = category
            , facet_col_wrap=4,
            title="Alfa diversidad "+ dataset + ' segun ' + category,
            height=1300,facet_col_spacing=0.04)
figbox.update_yaxes(matches=None)
figbox.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figbox.update_yaxes(showticklabels=True)
figbox.show()

In [11]:
figbox = px.box(complete, x=category, y=metrics,
             facet_col ="variable", color = category
            , facet_col_wrap=4,
            title="Alfa diversidad "+ dataset + ' segun ' + category,
            height=1300,facet_col_spacing=0.04,
               points='all')
figbox.update_yaxes(matches=None)
figbox.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figbox.update_yaxes(showticklabels=True)
figbox.show()

In [12]:
for metric in metrics:
    figvio = px.violin(complete, y=metric,
                       violinmode='overlay', color=category,
                      title = metric, points='all', box=True)
    figvio.show()

In [13]:
figecdf = px.ecdf(complete, x=metrics)
figecdf.show()

In [14]:
#Minmax normalization
norm_df2=complete
norm_df2[metrics]=(norm_df2[metrics]-norm_df2[metrics].min())/(norm_df2[metrics].max()-norm_df2[metrics].min())
figecdf2 = px.ecdf(norm_df2, x=metrics)
figecdf2.show()

In [15]:
figecdf3 = px.ecdf(norm_df2, x=metrics, facet_col= category)
figecdf3.show()

In [16]:
figecdf4 = px.ecdf(norm_df2, x=metrics, color= category,facet_col ="variable", facet_col_wrap=4, height=1000)
figecdf4.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figecdf4.show()

In [17]:
figvio = px.scatter(complete,
                    x='observed_features',
                    y=metrics,
            facet_col ="variable",
            color = category,
            facet_col_wrap=4,
            title="Alfa diversidad corr observed_features "+ dataset + ' segun ' + category,
            height=1300,)
figvio.update_yaxes(matches=None)
figvio.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figvio.show()

In [18]:
figvio = px.scatter(complete,
                    x='sample-frequency',
                    y=metrics,
            facet_col ="variable",
            color = category,
            facet_col_wrap=4,
            title="Alfa diversidad corr sample-frequency "+ dataset + ' segun ' + category,
            height=1300,)
figvio.update_yaxes(matches=None)
figvio.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figvio.show()

In [19]:
m1 = ['brillouin_d',  'heip_e',  'pielou_evenness', 'simpson', 'shannon_entropy']

m2 = ['ace', 'chao1' , 'goods_coverage', 'lladser_pe', 'menhinick' , 'robbins',  'doubles', 'singles', 'observed_features',
     'margalef','mcintosh_d' ]

m3 = [ 'berger_parker_d' , 'dominance', 'enspie', 'fisher_alpha',  'gini_index', 'strong']

figmatrix = px.scatter_matrix(complete,
            dimensions=m1,
            color = category,
            title="Correlaciones entre metricas de informacion "+ dataset + ' segun ' + category,
            height=1300)
figmatrix.update_yaxes(showticklabels=False)
#figvio.update_yaxes(matches=None)
#figvio.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figmatrix.show()

In [20]:
figmatrix = px.scatter_matrix(complete,
            dimensions=m2,
            color = category,
            title="Correlaciones entre metricas de abundancia"+ dataset + ' segun ' + category,
            height=1300)
figmatrix.update_yaxes(showticklabels=False)
#figvio.update_yaxes(matches=None)
#figvio.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figmatrix.show()

In [21]:
figmatrix = px.scatter_matrix(complete,
            dimensions=m3,
            color = category,
            title="Correlaciones entre metricas de dominancia "+ dataset + ' segun ' + category,
            height=1300)
figmatrix.update_yaxes(showticklabels=False)
#figvio.update_yaxes(matches=None)
#figvio.for_each_annotation(lambda a: a.update(text=a.text.split("=")[-1]))
figmatrix.show()

In [22]:
from scipy.stats import pearsonr

def calculate_pvalues(df):
    df = df.dropna()._get_numeric_data()
    dfcols = pd.DataFrame(columns=df.columns)
    pvalues = dfcols.transpose().join(dfcols, how='outer')
    for r in df.columns:
        for c in df.columns:
            pvalues[r][c] = round(pearsonr(df[r], df[c])[1], 4)
    return pvalues


#Calculo correlaciones
correlations_spearman = diversities.corr(method='spearman')
fig_heat_spearman = px.imshow(correlations_spearman,
                    title='Spearman correlation between metrics for ' + dataset)
fig_heat_spearman.show()

#Calculo significancia
pval_spearman = calculate_pvalues(diversities)
fig_heat_spearman_pval = px.imshow(pval_spearman,
                    title='pvalues for Spearman correlation between metrics for ' + dataset)
fig_heat_spearman_pval.show()

#display(pvalues_spearman)



In [23]:
### Export results to html
import subprocess 

try:
    subprocess.call('jupyter nbconvert --to html alphavis-single.ipynb', shell=True)
    #subprocess.call('mv alphavis-single.ipynb alphavis-single.'+dataset+'.html', shell=True)
except:
    print('oops')

[NbConvertApp] Converting notebook alphavis-single.ipynb to html
[NbConvertApp] Writing 2792653 bytes to alphavis-single.html


In [24]:
display(diversities)

sample-id         ace  berger_parker_d  brillouin_d       chao1  \
0    sample-129   88.549766         0.271275     3.106930   88.333333   
1    sample-287   88.000000         0.269825     3.038018   88.000000   
2    sample-197  218.569297         0.319665     3.242708  215.444444   
3    sample-489   63.000000         0.305966     2.585680   63.000000   
4    sample-516  331.487761         0.100289     4.451109  328.837838   
..          ...         ...              ...          ...         ...   
568  sample-547  141.058669         0.449145     2.445064  140.882353   
569  sample-337  114.038117         0.097931     3.637120  112.333333   
570   sample-82  125.967508         0.360709     2.629755  123.647059   
571  sample-148  127.681337         0.236174     3.388120  126.600000   
572   sample-18  145.156648         0.152089     3.601115  144.111111   

     dominance  doubles     enspie   faith_pd  fisher_alpha  ...  mcintosh_d  \
0     0.101662        2   9.836561   6.449248     11.878024  ...    0.686058   
1     0.100976        6   9.903308   5.819397     11.406183  ...    0.686526   
2     0.119166       26   8.391657   5.182606     32.007220  ...    0.659112   
3     0.130351       11   7.671615   5.060576      7.408508  ...    0.642319   
4     0.025792       36  38.772098  28.903686     60.879564  ...    0.846881   
..         ...      ...        ...        ...           ...  ...         ...   
568   0.238795       16   4.187696  15.497819     26.942505  ...    0.519228   
569   0.040169       11  24.894563   7.137584     18.574669  ...    0.809311   
570   0.167911       16   5.955538   4.364979     16.697521  ...    0.594113   
571   0.079921        9  12.512294   7.933618     17.610309  ...    0.722107   
572   0.056126        8  17.817044   8.876377     18.514732  ...    0.766839   

     menhinick  observed_features  pielou_evenness   robbins  shannon_entropy  \
0     0.628748                 88         0.696678  0.000102         4.500141   
1     0.550419                 88         0.680677  0.000000         4.396786   
2     1.381862                211         0.609626  0.000686         4.706981   
3     0.329577                 63         0.625200  0.000000         3.736995   
4     2.878875                326         0.778457  0.001170         6.499124   
..         ...                ...              ...       ...              ...   
568   2.082943                137         0.508517  0.002774         3.609470   
569   1.322999                110         0.781530  0.001157         5.299839   
570   0.790748                121         0.550777  0.000427         3.810752   
571   0.839441                126         0.703619  0.000178         4.909348   
572   0.699068                143         0.727567  0.000119         5.209289   

      simpson  singles    strong  sample-frequency  
0    0.898338        2  0.588787           19589.0  
1    0.899024        0  0.632433           25561.0  
2    0.880834       16  0.720033           23315.0  
3    0.869649        0  0.696086           36540.0  
4    0.974208       15  0.602220           12823.0  
..        ...      ...       ...               ...  
568  0.761205       12  0.732762            4326.0  
569  0.959831        8  0.571824            6913.0  
570  0.832089       10  0.750301           23415.0  
571  0.920079        4  0.615264           22530.0  
572  0.943874        5  0.613443           41844.0  

[573 rows x 25 columns]